<a href="https://colab.research.google.com/github/mhrice/soundsauce/blob/main/notebooks/Automated_Audio_Generation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# @title Imports and auth
!pip install --upgrade gupload
from google.colab import auth
auth.authenticate_user()
import gdown
import gspread
from google.auth import default

creds, _ = default()
gc = gspread.authorize(creds)
from google.oauth2.credentials import Credentials
from googleapiclient.discovery import build
from googleapiclient.http import MediaIoBaseDownload
from google_auth_oauthlib.flow import InstalledAppFlow
drive_downloader = build('drive', 'v3', credentials=creds)

import pandas as pd
import os
import glob
import torch
import torchaudio
!pip install -U audiocraft
from audiocraft.models import MusicGen
from audiocraft.data.audio import audio_write
from torch.utils.data import Dataset, DataLoader
from demucs import pretrained
from demucs.apply import apply_model
from demucs.audio import convert_audio
from tqdm import tqdm
import uuid
!pip install git+https://github.com/CPJKU/madmom
from madmom.features.key import CNNKeyRecognitionProcessor, key_prediction_to_label
from madmom.features.tempo import TempoEstimationProcessor
from madmom.features.beats import RNNBeatProcessor
import numpy as np
from datetime import date


  Using cached click-8.1.6-py3-none-any.whl (97 kB)
  Attempting uninstall: click
    Found existing installation: Click 7.0
    Uninstalling Click-7.0:
      Successfully uninstalled Click-7.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gupload 1.1.0 requires click==7.0, but you have click 8.1.6 which is incompatible.


  Cloning https://github.com/CPJKU/madmom to /tmp/pip-req-build-dc5csyck
  Running command git clone --filter=blob:none --quiet https://github.com/CPJKU/madmom /tmp/pip-req-build-dc5csyck
  Resolved https://github.com/CPJKU/madmom to commit 3bc8334099feb310acfce884ebdb76a28e01670d
  Running command git submodule update --init --recursive -q
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
# @title Setup musicgen, demucs, and madmom models
model = MusicGen.get_pretrained('melody')
model.set_generation_params(duration=10)
demucs = pretrained.get_model('htdemucs').to(model.device)
# Demucs stems to keep
stem2idx = {'drums': 0, 'bass': 1, 'other': 2, 'vocal': 3}
stem_idx = torch.LongTensor([stem2idx['vocal'], stem2idx['other'], stem2idx['bass']])

key_proc = CNNKeyRecognitionProcessor()
beats_proc = RNNBeatProcessor()
tempo_proc = TempoEstimationProcessor(fps=100, min_bpm=60, max_bpm=180)


Downloading: "https://dl.fbaipublicfiles.com/audiocraft/musicgen/v0/b0dbef54-37d256b525.th" to /root/.cache/torch/hub/checkpoints/b0dbef54-37d256b525.th
100%|██████████| 225M/225M [00:02<00:00, 106MB/s]
Downloading: "https://dl.fbaipublicfiles.com/audiocraft/musicgen/v0/f79af192-61305ffc49.th" to /root/.cache/torch/hub/checkpoints/f79af192-61305ffc49.th
100%|██████████| 2.58G/2.58G [00:26<00:00, 103MB/s] 
Downloading: "https://dl.fbaipublicfiles.com/demucs/hybrid_transformer/955717e8-8726e21a.th" to /root/.cache/torch/hub/checkpoints/955717e8-8726e21a.th
100%|██████████| 80.2M/80.2M [00:01<00:00, 69.4MB/s]


/usr/local/lib/python3.10/dist-packages/madmom/features/tempo.py:724: UserWarning: Usage of `method` is deprecated as of version 0.17. Please pass a dedicated `TempoHistogramProcessor` instance as `histogram_processor`.Functionality will be removed in version 0.19.
  warnings.warn(


In [ ]:
# @title Download Audio

if not os.path.exists("/content/data"):
  os.mkdir("/content/data")
%cd /content/data
google_drive_audio_folder_link = "https://drive.google.com/drive/folders/13dDzR48Z3mps85ENrhwrWnMS6gd686Qo" #@param {type:"string"}
# Example: https://drive.google.com/drive/u/1/folders/1egRkAv4OC5kVBBQ1fN-jtbImVCx8UUqw
gdown.download_folder(google_drive_audio_folder_link, remaining_ok=True)
%cd /content

/content/data


Retrieving folder list


Retrieving folder 1_kwNI-RdqFxAsSyouAAjDgTt5n7L6OeV @crushed_keyz - Loops with stems, bpm, key
Processing file 1O_nm9Iox-QTrO95KiK0hDAn3YwTVALYT 0. cKz! WAVY Cmin 90 bpm @crushed_keyz.mp3
Processing file 1hTYeiIoKMVSHpOob0CVe8j76CE4K9yX6 1. cKz! No tE VAYAS Fsharpmin 105 bpm @crushed_keyz 1.mp3
Processing file 1VGgkFaJ8KoIUWUom67BlmQD6s3vUCRb9 2. cKz! ICE Dmin 135 bpm @crushed_keyz.mp3
Processing file 1LHdJkTeAyg_IFj7DpSjjNWg1hviDtepU 3. cKz! Soulful Shadows Cmin 95 @crushed_key.mp3
Processing file 1BIYA_fHe9lr8BlhmeNy0arpAZ0hZUinp 4. cKz! Emotions Cmin 155 bpm @crushed_keyz x @justryda.mp3
Processing file 1ZnDJeeKUD35q2dYGx7TJhXzL2BsGLkIh 5. cKz! Depths Cmin 140 bpm @crushed_keyz x @justryda.mp3
Processing file 1nqModHN_lDVP24f2z597BjyQbMBGMZts 6. cKz! LowKey Cmin 100 bpm @crushed_keyz x @justryda.mp3
Processing file 1jtpQUpk1iw7SJ2JNnnRjTMQHdgzLxEZZ 6. cKz! Nasty - Reggaeton Bmin 170 bpm @crushed_keyz.mp3
Processing file 1-pGtzpU9nCl1AOpfJBix3oT1pGr_5pde 7. cKz! ICEBERG 124bpm @crush

KeyboardInterrupt: ignored

In [ ]:
# @title Dataset, dataloader
SAMPLE_RATE = 44100
class MusicgenPromptDataset(Dataset):
  def __init__(self, crop, gc):
    super().__init__()

    ## Load Spreadsheet
    spreadsheet_url = "https://docs.google.com/spreadsheets/d/1-_Jn9YVlxhxq2Cuug2N3U61bqyvTgrmsut1DQ6_h7Gk/edit#gid=767491867"
    worksheet = gc.open_by_url(spreadsheet_url).get_worksheet(1)
    # get_all_values gives a list of rows.
    data = worksheet.get_all_values()
    df = pd.DataFrame.from_records(data[1:])
    col1 = df[1]
    # Remove first row
    self.prompts = col1.tolist()
    ## Find Audio Files
    wav_filepaths = glob.glob("/content/data/**/*.wav", recursive=True)
    mp3_filepaths = glob.glob("/content/data/**/*.mp3", recursive=True)
    self.audio_filepaths = wav_filepaths + mp3_filepaths
    self.current_audio = None
    self.sample_rate = SAMPLE_RATE
    self.crop = crop

  def __len__(self):
    return len(self.audio_filepaths) * len(self.prompts)

  def __getitem__(self, idx):
    # Load new audio file only when looped through all prompts and all crops
    if idx % len(self.prompts) == 0:
      waveform_idx = idx // len(self.prompts)
      self.current_filename = self.audio_filepaths[waveform_idx]
      waveform, sample_rate = torchaudio.load(self.current_filename)
      # resample
      waveform = torchaudio.functional.resample(waveform, sample_rate, self.sample_rate)
      # Make mono
      waveform = torch.sum(waveform, dim=0, keepdim=True)
      # Crop waveform
      crop_start = self.sample_rate * self.crop[0]
      crop_end = self.sample_rate * self.crop[1]
      self.current_audio = waveform[:, crop_start:crop_end]

    prompt = self.prompts[idx % len(self.prompts)]
    return self.current_audio, prompt, self.current_filename


    # 20 waveforms, 10 prompts
    # 76 -> Waveform 7, prompt 6

    # 20 waveforms, 10 prompts, 3 crops
    # 76 -> Waveform 2, prompt 5, crop 1
    # 76 / (10 * 3) = 2
    # (76 / 3) % 10 = 5
    # 76 % 3 = 1


    ## Need crops outside




In [ ]:
# @title Generate Audio
if not os.path.exists("/content/outputs"):
  os.mkdir("/content/outputs")

crop = (0, 10)
model.set_generation_params(duration=10)

dataset = MusicgenPromptDataset(crop=crop, gc=gc)
dataloader = DataLoader(
    dataset,
    batch_size=7,
    shuffle=False,
    num_workers=0,
    collate_fn=None,
    pin_memory=False,
 )
print("Total generations:", len(dataset))

generation_params = model.generation_params
top_k = generation_params["top_k"]
top_p = generation_params["top_p"]
cfg_coef = generation_params["cfg_coef"]
temp = generation_params["temp"]
date = date.today()

metadata_url = "https://docs.google.com/spreadsheets/d/1OfH6dZW72GEIFd2_uc3QGQBfU0M5euNec2fyc17O5GU/edit#gid=0"
metadata_sheet = gc.open_by_url(metadata_url).sheet1
metadata = np.array(metadata_sheet.get_all_values())
for batch in tqdm(dataloader):
  audio, prompt, filename = batch
  wav = model.generate_with_chroma(prompt, audio, SAMPLE_RATE)
  for idx, out in enumerate(wav):
    # Bpm extract
    audio_write("/content/tmp", out.cpu(), model.sample_rate, strategy="loudness", format="mp3")
    try:
      act = beats_proc("/content/tmp.mp3")
      tempo_out = tempo_proc(act)
      tempo = round(tempo_out[0][0])
    except IndexError:
      tempo = 0
      print("BPM ERROR")
    # Key extract
    key_preds = key_proc(f"/content/tmp.mp3")
    key = key_prediction_to_label(key_preds)

    # Demucs
    wav = convert_audio(out, model.sample_rate, demucs.samplerate, demucs.audio_channels)
    wav = wav.unsqueeze(0)
    stems = apply_model(demucs, wav)
    stems = stems[:, stem_idx]  # extract stem
    stems = stems.sum(1)  # merge extracted stems
    stems = convert_audio(stems, demucs.samplerate, model.sample_rate, 1)
    demucs_output = stems[0]
    id = uuid.uuid1()
    output_path = f'/content/outputs/{id}'
    audio_write(output_path, demucs_output.cpu(), model.sample_rate, strategy="loudness", format="mp3")
    # Write audio to drive
    mp3_output_path = output_path+".mp3"
    !gupload --to "1bVxnnbUELQLfkpUXjaeON5BWkcn1wFIm" $mp3_output_path

    # Update metadata
    data = [str(id), prompt[idx], filename[idx], f"{crop[0]}-{crop[1]}", key, tempo, top_k, top_p, temp, cfg_coef, str(date)]
    metadata_sheet.append_row(data, table_range="A1:K1")

Total generations: 1950


  0%|          | 0/279 [00:00<?, ?it/s]CLIPPING /content/tmp happening with proba (a bit of clipping is okay): 0.0014125000452622771 maximum scale:  1.7692450284957886
CLIPPING /content/outputs/88a9c89c-2891-11ee-a325-0242ac1c000c happening with proba (a bit of clipping is okay): 0.00139999995008111 maximum scale:  1.753993272781372


Uploading file: /content/outputs/88a9c89c-2891-11ee-a325-0242ac1c000c.mp3 as: 88a9c89c-2891-11ee-a325-0242ac1c000c.mp3
Uploading file: /content/outputs/8db73a90-2891-11ee-a325-0242ac1c000c.mp3 as: 8db73a90-2891-11ee-a325-0242ac1c000c.mp3


CLIPPING /content/tmp happening with proba (a bit of clipping is okay): 0.0001250000059371814 maximum scale:  1.1271083354949951
CLIPPING /content/outputs/92e5b4ba-2891-11ee-a325-0242ac1c000c happening with proba (a bit of clipping is okay): 0.00014062499394640326 maximum scale:  1.1433688402175903


Uploading file: /content/outputs/92e5b4ba-2891-11ee-a325-0242ac1c000c.mp3 as: 92e5b4ba-2891-11ee-a325-0242ac1c000c.mp3
Uploading file: /content/outputs/987b3d32-2891-11ee-a325-0242ac1c000c.mp3 as: 987b3d32-2891-11ee-a325-0242ac1c000c.mp3


...

CLIPPING /content/tmp happening with proba (a bit of clipping is okay): 0.0008687499794177711 maximum scale:  1.491827130317688
CLIPPING /content/outputs/a3b5da18-2891-11ee-a325-0242ac1c000c happening with proba (a bit of clipping is okay): 0.0008812500163912773 maximum scale:  1.4939172267913818


Uploading file: /content/outputs/a3b5da18-2891-11ee-a325-0242ac1c000c.mp3 as: a3b5da18-2891-11ee-a325-0242ac1c000c.mp3


CLIPPING /content/tmp happening with proba (a bit of clipping is okay): 0.004800000227987766 maximum scale:  1.96209716796875
CLIPPING /content/outputs/a924a1a0-2891-11ee-a325-0242ac1c000c happening with proba (a bit of clipping is okay): 0.004737500101327896 maximum scale:  1.9525057077407837


Uploading file: /content/outputs/a924a1a0-2891-11ee-a325-0242ac1c000c.mp3 as: a924a1a0-2891-11ee-a325-0242ac1c000c.mp3


  0%|          | 0/279 [01:39<?, ?it/s]
